In [1]:
# import necessary packages
import super_gradients

[2023-06-28 13:55:09] INFO - crash_tips_setup.py - Crash tips is enabled. You can set your environment variable to CRASH_HANDLER=FALSE to disable it


The console stream is logged into /home/computervision_zl/sg_logs/console.log


/usr/local/lib/python3.8/dist-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.0
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [2]:
# initialize trainer
from super_gradients import Trainer
from super_gradients.training import MultiGPUMode

In [3]:
# importing models from supergradients
from super_gradients.training import models

model = models.get("yolo_nas_m", pretrained_weights="coco", num_classes=13)

In [4]:
# instantiate the dataset
from super_gradients.training.datasets.detection_datasets.coco_format_detection import COCOFormatDetectionDataset
from super_gradients.training.transforms.transforms import DetectionMosaic, DetectionRandomAffine, DetectionHSV, \
    DetectionHorizontalFlip, DetectionPaddedRescale, DetectionStandardize, DetectionTargetsFormatTransform
from super_gradients.training.utils.detection_utils import DetectionCollateFN
from super_gradients.training import dataloaders
from super_gradients.training.datasets.datasets_utils import worker_init_reset_seed


trainset = COCOFormatDetectionDataset(data_dir="dataset",
                                      images_dir="images/train",
                                      json_annotation_file="annotations/train_coco.json",
                                      input_dim=(640, 640),
                                      ignore_empty_annotations=False,
                                      transforms=[
                                          DetectionMosaic(prob=1., input_dim=(640, 640)),
                                          DetectionRandomAffine(degrees=0., scales=(0.5, 1.5), shear=0.,
                                                                target_size=(640, 640),
                                                                filter_box_candidates=False, border_value=128),
                                          DetectionHSV(prob=1., hgain=5, vgain=30, sgain=30),
                                          DetectionHorizontalFlip(prob=0.5),
                                          DetectionPaddedRescale(input_dim=(640, 640), max_targets=300),
                                          DetectionStandardize(max_value=255),
                                          DetectionTargetsFormatTransform(max_targets=300, input_dim=(640, 640),
                                                                          output_format="LABEL_CXCYWH")
                                      ])


valset = COCOFormatDetectionDataset(data_dir="dataset",
                                    images_dir="images/val",
                                    json_annotation_file="annotations/val_coco.json",
                                    input_dim=(640, 640),
                                    ignore_empty_annotations=False,
                                    transforms=[
                                        DetectionPaddedRescale(input_dim=(640, 640), max_targets=300),
                                        DetectionStandardize(max_value=255),
                                        DetectionTargetsFormatTransform(max_targets=300, input_dim=(640, 640),
                                                                        output_format="LABEL_CXCYWH")
                                    ])

loading annotations into memory...
Done (t=0.05s)
creating index...
index created!


Caching annotations:  89%|████████▉ | 3664/4097 [00:00<00:00, 7272.73it/s]

In [5]:
# configure dataloader
train_loader_8 = dataloaders.get(dataset=trainset, dataloader_params={
    "shuffle": True,
    "batch_size": 8,
    "num_workers": 8,
    "drop_last": False,
    "pin_memory": True,
    "collate_fn": DetectionCollateFN(),
    "worker_init_fn": worker_init_reset_seed,
    "min_samples": 512
})

valid_loader_8 = dataloaders.get(dataset=valset, dataloader_params={
    "shuffle": False,
    "batch_size": 8,
    "num_workers": 8,
    "drop_last": False,
    "pin_memory": True,
    "collate_fn": DetectionCollateFN(),
    "worker_init_fn": worker_init_reset_seed
})

train_loader_16 = dataloaders.get(dataset=trainset, dataloader_params={
    "shuffle": True,
    "batch_size": 16,
    "num_workers": 8,
    "drop_last": False,
    "pin_memory": True,
    "collate_fn": DetectionCollateFN(),
    "worker_init_fn": worker_init_reset_seed,
    "min_samples": 512
})

valid_loader_16 = dataloaders.get(dataset=valset, dataloader_params={
    "shuffle": False,
    "batch_size": 16,
    "num_workers": 8,
    "drop_last": False,
    "pin_memory": True,
    "collate_fn": DetectionCollateFN(),
    "worker_init_fn": worker_init_reset_seed
})

In [6]:
# training setup
from super_gradients.training import training_hyperparams
from super_gradients.training import dataloaders
# dataloader setup
from super_gradients.training.models.detection_models.pp_yolo_e import PPYoloEPostPredictionCallback
from pprint import pprint

from super_gradients.common.environment.cfg_utils import load_recipe

train_params_adam_001  = training_hyperparams.get('train_params_adam_001', recipes_dir_path="/home/computervision_zl/Documents/yolonas/")
train_params_adam_0001 = training_hyperparams.get('train_params_adam_0001', recipes_dir_path="/home/computervision_zl/Documents/yolonas/")
train_params_sgd_001   = training_hyperparams.get('train_params_sgd_001', recipes_dir_path="/home/computervision_zl/Documents/yolonas/")
train_params_sgd_0001  = training_hyperparams.get('train_params_sgd_0001', recipes_dir_path="/home/computervision_zl/Documents/yolonas/")

Caching annotations: 100%|██████████| 513/513 [00:00<00:00, 9425.15it/s]
/home/computervision_zl/.local/lib/python3.8/site-packages/hydra/_internal/defaults_list.py:251: UserWarning: In 'train_params_adam_001': Defaults list is missing `_self_`. See https://hydra.cc/docs/1.2/upgrades/1.0_to_1.1/default_composition_order for more information
  warnings.warn(msg, UserWarning)
/home/computervision_zl/.local/lib/python3.8/site-packages/hydra/_internal/defaults_list.py:251: UserWarning: In 'train_params_adam_0001': Defaults list is missing `_self_`. See https://hydra.cc/docs/1.2/upgrades/1.0_to_1.1/default_composition_order for more information
  warnings.warn(msg, UserWarning)


loading annotations into memory...
Done (t=0.01s)
creating index...
index created!


# Training

___________________

In [7]:
from time import sleep

# Hyperparameters
params = [
    {'batch': 8, 'lr': 0.001, 'optimizer': 'Adam'},
    {'batch': 8, 'lr': 0.001, 'optimizer': 'SGD'},
    {'batch': 8, 'lr': 0.01, 'optimizer': 'Adam'},
    {'batch': 8, 'lr': 0.01, 'optimizer': 'SGD'},
    {'batch': 16, 'lr': 0.001, 'optimizer': 'Adam'},
    {'batch': 16, 'lr': 0.001, 'optimizer': 'SGD'},
    {'batch': 16, 'lr': 0.01, 'optimizer': 'Adam'},
    {'batch': 16, 'lr': 0.01, 'optimizer': 'SGD'}
]

/home/computervision_zl/.local/lib/python3.8/site-packages/hydra/_internal/defaults_list.py:251: UserWarning: In 'train_params_sgd_001': Defaults list is missing `_self_`. See https://hydra.cc/docs/1.2/upgrades/1.0_to_1.1/default_composition_order for more information
  warnings.warn(msg, UserWarning)
/home/computervision_zl/.local/lib/python3.8/site-packages/hydra/_internal/defaults_list.py:251: UserWarning: In 'train_params_sgd_0001': Defaults list is missing `_self_`. See https://hydra.cc/docs/1.2/upgrades/1.0_to_1.1/default_composition_order for more information
  warnings.warn(msg, UserWarning)


In [8]:
# Experiment 1    {'batch': 8, 'lr': 0.001, 'optimizer': 'Adam'}
model = models.get("yolo_nas_m", pretrained_weights="coco", num_classes=13)

CHECKPOINT_DIR = 'notebook_ckpts/'
trainer = Trainer(experiment_name=f'YOLONAS_1', ckpt_root_dir=CHECKPOINT_DIR)

trainer.train(
    model=model, 
    training_params=train_params_adam_0001, 
    train_loader=train_loader_8, 
    valid_loader=valid_loader_8
    )

del trainer
sleep(5)

[2023-06-27 13:34:19] WARNING - sg_trainer.py - Train dataset size % batch_size != 0 and drop_last=False, this might result in smaller last batch.
W0627 13:34:19.412004 140657931003712 sg_trainer.py:1041] Train dataset size % batch_size != 0 and drop_last=False, this might result in smaller last batch.


The console stream is now moved to notebook_ckpts/YOLONAS_1/console_Jun27_13_34_21.txt


[2023-06-27 13:34:22] INFO - sg_trainer.py - Using EMA with params {'decay': 0.9997, 'decay_type': 'threshold', 'beta': 15}
[2023-06-27 13:34:23] INFO - sg_trainer_utils.py - TRAINING PARAMETERS:
    - Mode:                         Single GPU
    - Number of GPUs:               1          (1 available on the machine)
    - Dataset size:                 4097       (len(train_set))
    - Batch size per GPU:           8          (batch_size)
    - Batch Accumulate:             1          (batch_accumulate)
    - Total batch size:             8          (num_gpus * batch_size)
    - Effective Batch size:         8          (num_gpus * batch_size * batch_accumulate)
    - Iterations per epoch:         513        (len(train_loader))
    - Gradient updates per epoch:   513        (len(train_loader) / batch_accumulate)

[2023-06-27 13:34:23] INFO - sg_trainer.py - Started training for 150 epochs (0/149)

Validation epoch 0: 100%|██████████| 65/65 [00:06<00:00,  9.52it/s]


SUMMARY OF EPOCH 0
├── Training
│   ├── Ppyoloeloss/loss = 2.5364
│   ├── Ppyoloeloss/loss_cls = 1.3089
│   ├── Ppyoloeloss/loss_dfl = 1.3
│   └── Ppyoloeloss/loss_iou = 0.231
└── Validation
    ├── F1@0.50 = 0.0387
    ├── F1@0.50:0.95 = 0.025
    ├── Map@0.50 = 0.1806
    ├── Map@0.50:0.95 = 0.1015
    ├── Ppyoloeloss/loss = 2.335
    ├── Ppyoloeloss/loss_cls = 1.2044
    ├── Ppyoloeloss/loss_dfl = 1.2026
    ├── Ppyoloeloss/loss_iou = 0.2117
    ├── Precision@0.50 = 0.0209
    ├── Precision@0.50:0.95 = 0.0136
    ├── Recall@0.50 = 0.5996
    └── Recall@0.50:0.95 = 0.3462



[2023-06-27 13:36:13] INFO - base_sg_logger.py - Checkpoint saved in notebook_ckpts/YOLONAS_1/ckpt_best.pth
[2023-06-27 13:36:13] INFO - sg_trainer.py - Best checkpoint overriden: validation mAP@0.50: 0.18057700991630554
Validation epoch 1: 100%|██████████| 65/65 [00:06<00:00,  9.68it/s]


...

[2023-06-27 18:16:15] INFO - base_sg_logger.py - Checkpoint saved in notebook_ckpts/YOLONAS_1/ckpt_best.pth
[2023-06-27 18:16:15] INFO - sg_trainer.py - Best checkpoint overriden: validation mAP@0.50: 0.7668929696083069
Validation epoch 149: 100%|██████████| 65/65 [00:06<00:00,  9.70it/s]


SUMMARY OF EPOCH 149
├── Training
│   ├── Ppyoloeloss/loss = 1.4103
│   │   ├── Best until now = 1.4055 (↗ 0.0048)
│   │   └── Epoch N-1      = 1.4122 (↘ -0.002)
│   ├── Ppyoloeloss/loss_cls = 0.7185
│   │   ├── Best until now = 0.718  (↗ 0.0005)
│   │   └── Epoch N-1      = 0.7194 (↘ -0.0009)
│   ├── Ppyoloeloss/loss_dfl = 0.7925
│   │   ├── Best until now = 0.7886 (↗ 0.0038)
│   │   └── Epoch N-1      = 0.7938 (↘ -0.0013)
│   └── Ppyoloeloss/loss_iou = 0.1182
│       ├── Best until now = 0.1171 (↗ 0.0011)
│       └── Epoch N-1      = 0.1184 (↘ -0.0002)
└── Validation
    ├── F1@0.50 = 0.1936
    │   ├── Best until now = 0.1938 (↘ -0.0001)
    │   └── Epoch N-1      = 0.1929 (↗ 0.0008)
    ├── F1@0.50:0.95 = 0.1549
    │   ├── Best until now = 0.1545 (↗ 0.0004)
    │   └── Epoch N-1      = 0.1545 (↗ 0.0004)
    ├── Map@0.50 = 0.7678
    │   ├── Best until now = 0.7669 (↗ 0.0009)
    │   └── Epoch N-1      = 0.7669 (↗ 0.0009)
    ├── Map@0.50:0.95 = 0.5675
    │   ├── Best until now = 

[2023-06-27 18:18:10] INFO - base_sg_logger.py - Checkpoint saved in notebook_ckpts/YOLONAS_1/ckpt_best.pth
[2023-06-27 18:18:10] INFO - sg_trainer.py - Best checkpoint overriden: validation mAP@0.50: 0.7678261995315552
[2023-06-27 18:18:14] INFO - sg_trainer.py - RUNNING ADDITIONAL TEST ON THE AVERAGED MODEL...
Validation epoch 150: 100%|██████████| 65/65 [00:06<00:00,  9.66it/s]


SUMMARY OF EPOCH 150
├── Training
│   ├── Ppyoloeloss/loss = 1.4103
│   │   ├── Best until now = 1.4055 (↗ 0.0048)
│   │   └── Epoch N-1      = 1.4122 (↘ -0.002)
│   ├── Ppyoloeloss/loss_cls = 0.7185
│   │   ├── Best until now = 0.718  (↗ 0.0005)
│   │   └── Epoch N-1      = 0.7194 (↘ -0.0009)
│   ├── Ppyoloeloss/loss_dfl = 0.7925
│   │   ├── Best until now = 0.7886 (↗ 0.0038)
│   │   └── Epoch N-1      = 0.7938 (↘ -0.0013)
│   └── Ppyoloeloss/loss_iou = 0.1182
│       ├── Best until now = 0.1171 (↗ 0.0011)
│       └── Epoch N-1      = 0.1184 (↘ -0.0002)
└── Validation
    ├── F1@0.50 = 0.1918
    │   ├── Best until now = 0.1938 (↘ -0.0019)
    │   └── Epoch N-1      = 0.1936 (↘ -0.0018)
    ├── F1@0.50:0.95 = 0.1532
    │   ├── Best until now = 0.1549 (↘ -0.0017)
    │   └── Epoch N-1      = 0.1549 (↘ -0.0017)
    ├── Map@0.50 = 0.7614
    │   ├── Best until now = 0.7678 (↘ -0.0064)
    │   └── Epoch N-1      = 0.7678 (↘ -0.0064)
    ├── Map@0.50:0.95 = 0.564
    │   ├── Best until no

[2023-06-27 18:18:22] INFO - base_sg_logger.py - [CLEANUP] - Successfully stopped system monitoring process


In [9]:
# Experiment 2     {'batch': 8, 'lr': 0.001, 'optimizer': 'SGD'}
model = models.get("yolo_nas_m", pretrained_weights="coco", num_classes=13)

CHECKPOINT_DIR = 'notebook_ckpts/'
trainer = Trainer(experiment_name=f'YOLONAS_2', ckpt_root_dir=CHECKPOINT_DIR)

trainer.train(
    model=model, 
    training_params=train_params_sgd_0001, 
    train_loader=train_loader_8, 
    valid_loader=valid_loader_8
    )

del trainer
sleep(5)

[2023-06-27 18:18:27] INFO - checkpoint_utils.py - License Notification: YOLO-NAS pre-trained weights are subjected to the specific license terms and conditions detailed in 
https://github.com/Deci-AI/super-gradients/blob/master/LICENSE.YOLONAS.md
By downloading the pre-trained weight files you agree to comply with these terms.
[2023-06-27 18:18:27] WARNING - sg_trainer.py - Train dataset size % batch_size != 0 and drop_last=False, this might result in smaller last batch.


The console stream is now moved to notebook_ckpts/YOLONAS_2/console_Jun27_18_18_27.txt


[2023-06-27 18:18:28] INFO - sg_trainer.py - Using EMA with params {'decay': 0.9997, 'decay_type': 'threshold', 'beta': 15}
[2023-06-27 18:18:29] INFO - sg_trainer_utils.py - TRAINING PARAMETERS:
    - Mode:                         Single GPU
    - Number of GPUs:               1          (1 available on the machine)
    - Dataset size:                 4097       (len(train_set))
    - Batch size per GPU:           8          (batch_size)
    - Batch Accumulate:             1          (batch_accumulate)
    - Total batch size:             8          (num_gpus * batch_size)
    - Effective Batch size:         8          (num_gpus * batch_size * batch_accumulate)
    - Iterations per epoch:         513        (len(train_loader))
    - Gradient updates per epoch:   513        (len(train_loader) / batch_accumulate)

[2023-06-27 18:18:29] INFO - sg_trainer.py - Started training for 150 epochs (0/149)

Validation epoch 0: 100%|██████████| 65/65 [00:06<00:00,  9.35it/s]


SUMMARY OF EPOCH 0
├── Training
│   ├── Ppyoloeloss/loss = 2.0143
│   ├── Ppyoloeloss/loss_cls = 1.1747
│   ├── Ppyoloeloss/loss_dfl = 0.9226
│   └── Ppyoloeloss/loss_iou = 0.1513
└── Validation
    ├── F1@0.50 = 0.1488
    ├── F1@0.50:0.95 = 0.1166
    ├── Map@0.50 = 0.522
    ├── Map@0.50:0.95 = 0.379
    ├── Ppyoloeloss/loss = 1.7053
    ├── Ppyoloeloss/loss_cls = 0.9077
    ├── Ppyoloeloss/loss_dfl = 0.92
    ├── Ppyoloeloss/loss_iou = 0.1351
    ├── Precision@0.50 = 0.0874
    ├── Precision@0.50:0.95 = 0.0692
    ├── Recall@0.50 = 0.8023
    └── Recall@0.50:0.95 = 0.5901



[2023-06-27 18:20:06] INFO - base_sg_logger.py - Checkpoint saved in notebook_ckpts/YOLONAS_2/ckpt_best.pth
[2023-06-27 18:20:06] INFO - sg_trainer.py - Best checkpoint overriden: validation mAP@0.50: 0.5220344662666321
Validation epoch 1: 100%|██████████| 65/65 [00:06<00:00,  9.41it/s]


...

Validation epoch 149: 100%|██████████| 65/65 [00:06<00:00, 10.12it/s]


SUMMARY OF EPOCH 149
├── Training
│   ├── Ppyoloeloss/loss = 1.1783
│   │   ├── Best until now = 1.0162 (↗ 0.162)
│   │   └── Epoch N-1      = 1.028  (↗ 0.1503)
│   ├── Ppyoloeloss/loss_cls = 0.5828
│   │   ├── Best until now = 0.492  (↗ 0.0908)
│   │   └── Epoch N-1      = 0.5012 (↗ 0.0816)
│   ├── Ppyoloeloss/loss_dfl = 0.7146
│   │   ├── Best until now = 0.6588 (↗ 0.0558)
│   │   └── Epoch N-1      = 0.6633 (↗ 0.0513)
│   └── Ppyoloeloss/loss_iou = 0.0953
│       ├── Best until now = 0.077  (↗ 0.0183)
│       └── Epoch N-1      = 0.0781 (↗ 0.0172)
└── Validation
    ├── F1@0.50 = 0.5532
    │   ├── Best until now = 0.5808 (↘ -0.0276)
    │   └── Epoch N-1      = 0.5808 (↘ -0.0276)
    ├── F1@0.50:0.95 = 0.4614
    │   ├── Best until now = 0.4921 (↘ -0.0307)
    │   └── Epoch N-1      = 0.4921 (↘ -0.0307)
    ├── Map@0.50 = 0.8793
    │   ├── Best until now = 0.8879 (↘ -0.0086)
    │   └── Epoch N-1      = 0.8842 (↘ -0.0049)
    ├── Map@0.50:0.95 = 0.692
    │   ├── Best until now = 

[2023-06-27 22:31:51] INFO - sg_trainer.py - RUNNING ADDITIONAL TEST ON THE AVERAGED MODEL...
Validation epoch 150: 100%|██████████| 65/65 [00:06<00:00,  9.94it/s]


SUMMARY OF EPOCH 150
├── Training
│   ├── Ppyoloeloss/loss = 1.1783
│   │   ├── Best until now = 1.0162 (↗ 0.162)
│   │   └── Epoch N-1      = 1.028  (↗ 0.1503)
│   ├── Ppyoloeloss/loss_cls = 0.5828
│   │   ├── Best until now = 0.492  (↗ 0.0908)
│   │   └── Epoch N-1      = 0.5012 (↗ 0.0816)
│   ├── Ppyoloeloss/loss_dfl = 0.7146
│   │   ├── Best until now = 0.6588 (↗ 0.0558)
│   │   └── Epoch N-1      = 0.6633 (↗ 0.0513)
│   └── Ppyoloeloss/loss_iou = 0.0953
│       ├── Best until now = 0.077  (↗ 0.0183)
│       └── Epoch N-1      = 0.0781 (↗ 0.0172)
└── Validation
    ├── F1@0.50 = 0.5269
    │   ├── Best until now = 0.5808 (↘ -0.0538)
    │   └── Epoch N-1      = 0.5532 (↘ -0.0262)
    ├── F1@0.50:0.95 = 0.4483
    │   ├── Best until now = 0.4921 (↘ -0.0438)
    │   └── Epoch N-1      = 0.4614 (↘ -0.0131)
    ├── Map@0.50 = 0.8852
    │   ├── Best until now = 0.8879 (↘ -0.0026)
    │   └── Epoch N-1      = 0.8793 (↗ 0.0059)
    ├── Map@0.50:0.95 = 0.7003
    │   ├── Best until now = 

[2023-06-27 22:31:58] INFO - base_sg_logger.py - [CLEANUP] - Successfully stopped system monitoring process


In [10]:
# Experiment 3    {'batch': 8, 'lr': 0.01, 'optimizer': 'Adam'}
model = models.get("yolo_nas_m", pretrained_weights="coco", num_classes=13)

CHECKPOINT_DIR = 'notebook_ckpts/'
trainer = Trainer(experiment_name=f'YOLONAS_3', ckpt_root_dir=CHECKPOINT_DIR)

trainer.train(
    model=model, 
    training_params=train_params_adam_001, 
    train_loader=train_loader_8, 
    valid_loader=valid_loader_8
    )

del trainer
sleep(5)

[2023-06-27 22:32:03] INFO - checkpoint_utils.py - License Notification: YOLO-NAS pre-trained weights are subjected to the specific license terms and conditions detailed in 
https://github.com/Deci-AI/super-gradients/blob/master/LICENSE.YOLONAS.md
By downloading the pre-trained weight files you agree to comply with these terms.
[2023-06-27 22:32:03] WARNING - sg_trainer.py - Train dataset size % batch_size != 0 and drop_last=False, this might result in smaller last batch.


The console stream is now moved to notebook_ckpts/YOLONAS_3/console_Jun27_22_32_03.txt


[2023-06-27 22:32:04] INFO - sg_trainer.py - Using EMA with params {'decay': 0.9997, 'decay_type': 'threshold', 'beta': 15}
[2023-06-27 22:32:05] INFO - sg_trainer_utils.py - TRAINING PARAMETERS:
    - Mode:                         Single GPU
    - Number of GPUs:               1          (1 available on the machine)
    - Dataset size:                 4097       (len(train_set))
    - Batch size per GPU:           8          (batch_size)
    - Batch Accumulate:             1          (batch_accumulate)
    - Total batch size:             8          (num_gpus * batch_size)
    - Effective Batch size:         8          (num_gpus * batch_size * batch_accumulate)
    - Iterations per epoch:         513        (len(train_loader))
    - Gradient updates per epoch:   513        (len(train_loader) / batch_accumulate)

[2023-06-27 22:32:05] INFO - sg_trainer.py - Started training for 150 epochs (0/149)

Validation epoch 0: 100%|██████████| 65/65 [00:07<00:00,  8.96it/s]


SUMMARY OF EPOCH 0
├── Training
│   ├── Ppyoloeloss/loss = 3.752
│   ├── Ppyoloeloss/loss_cls = 1.5626
│   ├── Ppyoloeloss/loss_dfl = 2.1083
│   └── Ppyoloeloss/loss_iou = 0.4541
└── Validation
    ├── F1@0.50 = 0.0054
    ├── F1@0.50:0.95 = 0.0025
    ├── Map@0.50 = 0.0231
    ├── Map@0.50:0.95 = 0.0068
    ├── Ppyoloeloss/loss = 3.4878
    ├── Ppyoloeloss/loss_cls = 1.5036
    ├── Ppyoloeloss/loss_dfl = 1.9193
    ├── Ppyoloeloss/loss_iou = 0.4098
    ├── Precision@0.50 = 0.0094
    ├── Precision@0.50:0.95 = 0.0032
    ├── Recall@0.50 = 0.1933
    └── Recall@0.50:0.95 = 0.0889



[2023-06-27 22:33:55] INFO - base_sg_logger.py - Checkpoint saved in notebook_ckpts/YOLONAS_3/ckpt_best.pth
[2023-06-27 22:33:55] INFO - sg_trainer.py - Best checkpoint overriden: validation mAP@0.50: 0.02312960848212242
Validation epoch 1: 100%|██████████| 65/65 [00:07<00:00,  8.83it/s]


...

[2023-06-28 03:14:54] INFO - base_sg_logger.py - Checkpoint saved in notebook_ckpts/YOLONAS_3/ckpt_best.pth
[2023-06-28 03:14:54] INFO - sg_trainer.py - Best checkpoint overriden: validation mAP@0.50: 0.394317090511322
Validation epoch 149: 100%|██████████| 65/65 [00:07<00:00,  9.25it/s]


SUMMARY OF EPOCH 149
├── Training
│   ├── Ppyoloeloss/loss = 1.9396
│   │   ├── Best until now = 1.9218 (↗ 0.0179)
│   │   └── Epoch N-1      = 1.9335 (↗ 0.0061)
│   ├── Ppyoloeloss/loss_cls = 1.0038
│   │   ├── Best until now = 0.9933 (↗ 0.0105)
│   │   └── Epoch N-1      = 0.9961 (↗ 0.0077)
│   ├── Ppyoloeloss/loss_dfl = 1.0126
│   │   ├── Best until now = 1.0039 (↗ 0.0087)
│   │   └── Epoch N-1      = 1.0124 (↗ 0.0002)
│   └── Ppyoloeloss/loss_iou = 0.1718
│       ├── Best until now = 0.1704 (↗ 0.0014)
│       └── Epoch N-1      = 0.1725 (↘ -0.0007)
└── Validation
    ├── F1@0.50 = 0.0986
    │   ├── Best until now = 0.1013 (↘ -0.0027)
    │   └── Epoch N-1      = 0.0992 (↘ -0.0006)
    ├── F1@0.50:0.95 = 0.0723
    │   ├── Best until now = 0.0735 (↘ -0.0012)
    │   └── Epoch N-1      = 0.0727 (↘ -0.0004)
    ├── Map@0.50 = 0.3935
    │   ├── Best until now = 0.3943 (↘ -0.0008)
    │   └── Epoch N-1      = 0.3943 (↘ -0.0008)
    ├── Map@0.50:0.95 = 0.2614
    │   ├── Best until now

[2023-06-28 03:16:52] INFO - sg_trainer.py - RUNNING ADDITIONAL TEST ON THE AVERAGED MODEL...
Validation epoch 150: 100%|██████████| 65/65 [00:06<00:00,  9.34it/s]


SUMMARY OF EPOCH 150
├── Training
│   ├── Ppyoloeloss/loss = 1.9396
│   │   ├── Best until now = 1.9218 (↗ 0.0179)
│   │   └── Epoch N-1      = 1.9335 (↗ 0.0061)
│   ├── Ppyoloeloss/loss_cls = 1.0038
│   │   ├── Best until now = 0.9933 (↗ 0.0105)
│   │   └── Epoch N-1      = 0.9961 (↗ 0.0077)
│   ├── Ppyoloeloss/loss_dfl = 1.0126
│   │   ├── Best until now = 1.0039 (↗ 0.0087)
│   │   └── Epoch N-1      = 1.0124 (↗ 0.0002)
│   └── Ppyoloeloss/loss_iou = 0.1718
│       ├── Best until now = 0.1704 (↗ 0.0014)
│       └── Epoch N-1      = 0.1725 (↘ -0.0007)
└── Validation
    ├── F1@0.50 = 0.1008
    │   ├── Best until now = 0.1013 (↘ -0.0005)
    │   └── Epoch N-1      = 0.0986 (↗ 0.0022)
    ├── F1@0.50:0.95 = 0.0736
    │   ├── Best until now = 0.0735 (↗ 0.0001)
    │   └── Epoch N-1      = 0.0723 (↗ 0.0013)
    ├── Map@0.50 = 0.3903
    │   ├── Best until now = 0.3943 (↘ -0.0041)
    │   └── Epoch N-1      = 0.3935 (↘ -0.0032)
    ├── Map@0.50:0.95 = 0.2572
    │   ├── Best until now = 

[2023-06-28 03:17:00] INFO - base_sg_logger.py - [CLEANUP] - Successfully stopped system monitoring process


In [11]:
# Experiment 4    {'batch': 8, 'lr': 0.01, 'optimizer': 'SGD'}
model = models.get("yolo_nas_m", pretrained_weights="coco", num_classes=13)

CHECKPOINT_DIR = 'notebook_ckpts/'
trainer = Trainer(experiment_name=f'YOLONAS_4', ckpt_root_dir=CHECKPOINT_DIR)

trainer.train(
    model=model, 
    training_params=train_params_sgd_001, 
    train_loader=train_loader_8, 
    valid_loader=valid_loader_8
    )

del trainer
sleep(5)

[2023-06-28 03:17:05] INFO - checkpoint_utils.py - License Notification: YOLO-NAS pre-trained weights are subjected to the specific license terms and conditions detailed in 
https://github.com/Deci-AI/super-gradients/blob/master/LICENSE.YOLONAS.md
By downloading the pre-trained weight files you agree to comply with these terms.
[2023-06-28 03:17:06] WARNING - sg_trainer.py - Train dataset size % batch_size != 0 and drop_last=False, this might result in smaller last batch.


The console stream is now moved to notebook_ckpts/YOLONAS_4/console_Jun28_03_17_06.txt


[2023-06-28 03:17:06] INFO - sg_trainer.py - Using EMA with params {'decay': 0.9997, 'decay_type': 'threshold', 'beta': 15}
[2023-06-28 03:17:07] INFO - sg_trainer_utils.py - TRAINING PARAMETERS:
    - Mode:                         Single GPU
    - Number of GPUs:               1          (1 available on the machine)
    - Dataset size:                 4097       (len(train_set))
    - Batch size per GPU:           8          (batch_size)
    - Batch Accumulate:             1          (batch_accumulate)
    - Total batch size:             8          (num_gpus * batch_size)
    - Effective Batch size:         8          (num_gpus * batch_size * batch_accumulate)
    - Iterations per epoch:         513        (len(train_loader))
    - Gradient updates per epoch:   513        (len(train_loader) / batch_accumulate)

[2023-06-28 03:17:07] INFO - sg_trainer.py - Started training for 150 epochs (0/149)

Validation epoch 0: 100%|██████████| 65/65 [00:07<00:00,  8.89it/s]


SUMMARY OF EPOCH 0
├── Training
│   ├── Ppyoloeloss/loss = 2.7988
│   ├── Ppyoloeloss/loss_cls = 1.3695
│   ├── Ppyoloeloss/loss_dfl = 1.4731
│   └── Ppyoloeloss/loss_iou = 0.2771
└── Validation
    ├── F1@0.50 = 0.0332
    ├── F1@0.50:0.95 = 0.0225
    ├── Map@0.50 = 0.1499
    ├── Map@0.50:0.95 = 0.0843
    ├── Ppyoloeloss/loss = 2.4742
    ├── Ppyoloeloss/loss_cls = 1.2462
    ├── Ppyoloeloss/loss_dfl = 1.2799
    ├── Ppyoloeloss/loss_iou = 0.2352
    ├── Precision@0.50 = 0.019
    ├── Precision@0.50:0.95 = 0.0127
    ├── Recall@0.50 = 0.4877
    └── Recall@0.50:0.95 = 0.2829



[2023-06-28 03:18:45] INFO - base_sg_logger.py - Checkpoint saved in notebook_ckpts/YOLONAS_4/ckpt_best.pth
[2023-06-28 03:18:45] INFO - sg_trainer.py - Best checkpoint overriden: validation mAP@0.50: 0.1498633176088333
Validation epoch 1: 100%|██████████| 65/65 [00:07<00:00,  9.23it/s]


...

Validation epoch 149: 100%|██████████| 65/65 [00:06<00:00,  9.71it/s]


SUMMARY OF EPOCH 149
├── Training
│   ├── Ppyoloeloss/loss = 1.2848
│   │   ├── Best until now = 1.28   (↗ 0.0048)
│   │   └── Epoch N-1      = 1.2818 (↗ 0.003)
│   ├── Ppyoloeloss/loss_cls = 0.6409
│   │   ├── Best until now = 0.6373 (↗ 0.0036)
│   │   └── Epoch N-1      = 0.6386 (↗ 0.0023)
│   ├── Ppyoloeloss/loss_dfl = 0.7395
│   │   ├── Best until now = 0.7365 (↗ 0.003)
│   │   └── Epoch N-1      = 0.7394 (↗ 1e-04)
│   └── Ppyoloeloss/loss_iou = 0.1097
│       ├── Best until now = 0.1088 (↗ 0.0008)
│       └── Epoch N-1      = 0.1094 (↗ 0.0002)
└── Validation
    ├── F1@0.50 = 0.2608
    │   ├── Best until now = 0.2601 (↗ 0.0007)
    │   └── Epoch N-1      = 0.2601 (↗ 0.0007)
    ├── F1@0.50:0.95 = 0.2177
    │   ├── Best until now = 0.2173 (↗ 0.0004)
    │   └── Epoch N-1      = 0.2173 (↗ 0.0004)
    ├── Map@0.50 = 0.8072
    │   ├── Best until now = 0.8093 (↘ -0.0021)
    │   └── Epoch N-1      = 0.8078 (↘ -0.0005)
    ├── Map@0.50:0.95 = 0.6201
    │   ├── Best until now = 0.621

[2023-06-28 07:31:59] INFO - sg_trainer.py - RUNNING ADDITIONAL TEST ON THE AVERAGED MODEL...
Validation epoch 150: 100%|██████████| 65/65 [00:06<00:00,  9.81it/s]


SUMMARY OF EPOCH 150
├── Training
│   ├── Ppyoloeloss/loss = 1.2848
│   │   ├── Best until now = 1.28   (↗ 0.0048)
│   │   └── Epoch N-1      = 1.2818 (↗ 0.003)
│   ├── Ppyoloeloss/loss_cls = 0.6409
│   │   ├── Best until now = 0.6373 (↗ 0.0036)
│   │   └── Epoch N-1      = 0.6386 (↗ 0.0023)
│   ├── Ppyoloeloss/loss_dfl = 0.7395
│   │   ├── Best until now = 0.7365 (↗ 0.003)
│   │   └── Epoch N-1      = 0.7394 (↗ 1e-04)
│   └── Ppyoloeloss/loss_iou = 0.1097
│       ├── Best until now = 0.1088 (↗ 0.0008)
│       └── Epoch N-1      = 0.1094 (↗ 0.0002)
└── Validation
    ├── F1@0.50 = 0.2578
    │   ├── Best until now = 0.2608 (↘ -0.0029)
    │   └── Epoch N-1      = 0.2608 (↘ -0.0029)
    ├── F1@0.50:0.95 = 0.215
    │   ├── Best until now = 0.2177 (↘ -0.0027)
    │   └── Epoch N-1      = 0.2177 (↘ -0.0027)
    ├── Map@0.50 = 0.8085
    │   ├── Best until now = 0.8093 (↘ -0.0008)
    │   └── Epoch N-1      = 0.8072 (↗ 0.0013)
    ├── Map@0.50:0.95 = 0.62
    │   ├── Best until now = 0.621

[2023-06-28 07:32:06] INFO - base_sg_logger.py - [CLEANUP] - Successfully stopped system monitoring process


In [8]:
# Experiment 5    {'batch': 16, 'lr': 0.001, 'optimizer': 'Adam'}
model = models.get("yolo_nas_m", pretrained_weights="coco", num_classes=13)

CHECKPOINT_DIR = 'notebook_ckpts/'
trainer = Trainer(experiment_name=f'YOLONAS_5', ckpt_root_dir=CHECKPOINT_DIR)

trainer.train(
    model=model, 
    training_params=train_params_adam_0001, 
    train_loader=train_loader_16, 
    valid_loader=valid_loader_16
    )

del trainer
sleep(5)

[2023-06-28 13:55:28] WARNING - sg_trainer.py - Train dataset size % batch_size != 0 and drop_last=False, this might result in smaller last batch.
W0628 13:55:28.970968 140563797055296 sg_trainer.py:1041] Train dataset size % batch_size != 0 and drop_last=False, this might result in smaller last batch.


The console stream is now moved to notebook_ckpts/YOLONAS_5/console_Jun28_13_55_31.txt


[2023-06-28 13:55:32] INFO - sg_trainer.py - Using EMA with params {'decay': 0.9997, 'decay_type': 'threshold', 'beta': 15}
[2023-06-28 13:55:34] INFO - sg_trainer_utils.py - TRAINING PARAMETERS:
    - Mode:                         Single GPU
    - Number of GPUs:               1          (1 available on the machine)
    - Dataset size:                 4097       (len(train_set))
    - Batch size per GPU:           16         (batch_size)
    - Batch Accumulate:             1          (batch_accumulate)
    - Total batch size:             16         (num_gpus * batch_size)
    - Effective Batch size:         16         (num_gpus * batch_size * batch_accumulate)
    - Iterations per epoch:         257        (len(train_loader))
    - Gradient updates per epoch:   257        (len(train_loader) / batch_accumulate)

[2023-06-28 13:55:34] INFO - sg_trainer.py - Started training for 150 epochs (0/149)

Validation epoch 0: 100%|██████████| 33/33 [00:10<00:00,  3.00it/s]


SUMMARY OF EPOCH 0
├── Training
│   ├── Ppyoloeloss/loss = 2.3918
│   ├── Ppyoloeloss/loss_cls = 1.2852
│   ├── Ppyoloeloss/loss_dfl = 1.1772
│   └── Ppyoloeloss/loss_iou = 0.2072
└── Validation
    ├── F1@0.50 = 0.0373
    ├── F1@0.50:0.95 = 0.0233
    ├── Map@0.50 = 0.1988
    ├── Map@0.50:0.95 = 0.1152
    ├── Ppyoloeloss/loss = 2.3086
    ├── Ppyoloeloss/loss_cls = 1.2092
    ├── Ppyoloeloss/loss_dfl = 1.1847
    ├── Ppyoloeloss/loss_iou = 0.2028
    ├── Precision@0.50 = 0.0201
    ├── Precision@0.50:0.95 = 0.0125
    ├── Recall@0.50 = 0.6198
    └── Recall@0.50:0.95 = 0.3706



[2023-06-28 13:57:25] INFO - base_sg_logger.py - Checkpoint saved in notebook_ckpts/YOLONAS_5/ckpt_best.pth
[2023-06-28 13:57:25] INFO - sg_trainer.py - Best checkpoint overriden: validation mAP@0.50: 0.1988123059272766
Validation epoch 1: 100%|██████████| 33/33 [00:06<00:00,  4.98it/s]


...

[2023-06-28 18:10:09] INFO - base_sg_logger.py - Checkpoint saved in notebook_ckpts/YOLONAS_5/ckpt_best.pth
[2023-06-28 18:10:09] INFO - sg_trainer.py - Best checkpoint overriden: validation mAP@0.50: 0.7809158563613892
Validation epoch 149: 100%|██████████| 33/33 [00:18<00:00,  1.75it/s]


SUMMARY OF EPOCH 149
├── Training
│   ├── Ppyoloeloss/loss = 1.3552
│   │   ├── Best until now = 1.3574 (↘ -0.0022)
│   │   └── Epoch N-1      = 1.3596 (↘ -0.0044)
│   ├── Ppyoloeloss/loss_cls = 0.6886
│   │   ├── Best until now = 0.6881 (↗ 0.0005)
│   │   └── Epoch N-1      = 0.6881 (↗ 0.0005)
│   ├── Ppyoloeloss/loss_dfl = 0.7676
│   │   ├── Best until now = 0.7682 (↘ -0.0006)
│   │   └── Epoch N-1      = 0.7717 (↘ -0.0042)
│   └── Ppyoloeloss/loss_iou = 0.1131
│       ├── Best until now = 0.1136 (↘ -0.0004)
│       └── Epoch N-1      = 0.1142 (↘ -0.0011)
└── Validation
    ├── F1@0.50 = 0.2319
    │   ├── Best until now = 0.2309 (↗ 0.0009)
    │   └── Epoch N-1      = 0.2309 (↗ 0.0009)
    ├── F1@0.50:0.95 = 0.1895
    │   ├── Best until now = 0.1883 (↗ 0.0011)
    │   └── Epoch N-1      = 0.1883 (↗ 0.0011)
    ├── Map@0.50 = 0.7819
    │   ├── Best until now = 0.7809 (↗ 0.001)
    │   └── Epoch N-1      = 0.7809 (↗ 0.001)
    ├── Map@0.50:0.95 = 0.5779
    │   ├── Best until now = 

[2023-06-28 18:12:13] INFO - base_sg_logger.py - Checkpoint saved in notebook_ckpts/YOLONAS_5/ckpt_best.pth
[2023-06-28 18:12:13] INFO - sg_trainer.py - Best checkpoint overriden: validation mAP@0.50: 0.7818920612335205
[2023-06-28 18:12:18] INFO - sg_trainer.py - RUNNING ADDITIONAL TEST ON THE AVERAGED MODEL...
Validation epoch 150: 100%|██████████| 33/33 [00:18<00:00,  1.74it/s]


SUMMARY OF EPOCH 150
├── Training
│   ├── Ppyoloeloss/loss = 1.3552
│   │   ├── Best until now = 1.3574 (↘ -0.0022)
│   │   └── Epoch N-1      = 1.3596 (↘ -0.0044)
│   ├── Ppyoloeloss/loss_cls = 0.6886
│   │   ├── Best until now = 0.6881 (↗ 0.0005)
│   │   └── Epoch N-1      = 0.6881 (↗ 0.0005)
│   ├── Ppyoloeloss/loss_dfl = 0.7676
│   │   ├── Best until now = 0.7682 (↘ -0.0006)
│   │   └── Epoch N-1      = 0.7717 (↘ -0.0042)
│   └── Ppyoloeloss/loss_iou = 0.1131
│       ├── Best until now = 0.1136 (↘ -0.0004)
│       └── Epoch N-1      = 0.1142 (↘ -0.0011)
└── Validation
    ├── F1@0.50 = 0.2293
    │   ├── Best until now = 0.2319 (↘ -0.0026)
    │   └── Epoch N-1      = 0.2319 (↘ -0.0026)
    ├── F1@0.50:0.95 = 0.1863
    │   ├── Best until now = 0.1895 (↘ -0.0032)
    │   └── Epoch N-1      = 0.1895 (↘ -0.0032)
    ├── Map@0.50 = 0.7793
    │   ├── Best until now = 0.7819 (↘ -0.0026)
    │   └── Epoch N-1      = 0.7819 (↘ -0.0026)
    ├── Map@0.50:0.95 = 0.5739
    │   ├── Best unti

[2023-06-28 18:12:38] INFO - base_sg_logger.py - [CLEANUP] - Successfully stopped system monitoring process


In [9]:
# Experiment 6    {'batch': 16, 'lr': 0.001, 'optimizer': 'SGD'}
model = models.get("yolo_nas_m", pretrained_weights="coco", num_classes=13)

CHECKPOINT_DIR = 'notebook_ckpts/'
trainer = Trainer(experiment_name=f'YOLONAS_6', ckpt_root_dir=CHECKPOINT_DIR)

trainer.train(
    model=model, 
    training_params=train_params_sgd_0001, 
    train_loader=train_loader_16, 
    valid_loader=valid_loader_16
    )

del trainer
sleep(5)

[2023-06-28 18:12:43] INFO - checkpoint_utils.py - License Notification: YOLO-NAS pre-trained weights are subjected to the specific license terms and conditions detailed in 
https://github.com/Deci-AI/super-gradients/blob/master/LICENSE.YOLONAS.md
By downloading the pre-trained weight files you agree to comply with these terms.
[2023-06-28 18:12:44] WARNING - sg_trainer.py - Train dataset size % batch_size != 0 and drop_last=False, this might result in smaller last batch.


The console stream is now moved to notebook_ckpts/YOLONAS_6/console_Jun28_18_12_44.txt


[2023-06-28 18:12:44] INFO - sg_trainer.py - Using EMA with params {'decay': 0.9997, 'decay_type': 'threshold', 'beta': 15}
[2023-06-28 18:12:46] INFO - sg_trainer_utils.py - TRAINING PARAMETERS:
    - Mode:                         Single GPU
    - Number of GPUs:               1          (1 available on the machine)
    - Dataset size:                 4097       (len(train_set))
    - Batch size per GPU:           16         (batch_size)
    - Batch Accumulate:             1          (batch_accumulate)
    - Total batch size:             16         (num_gpus * batch_size)
    - Effective Batch size:         16         (num_gpus * batch_size * batch_accumulate)
    - Iterations per epoch:         257        (len(train_loader))
    - Gradient updates per epoch:   257        (len(train_loader) / batch_accumulate)

[2023-06-28 18:12:46] INFO - sg_trainer.py - Started training for 150 epochs (0/149)

Validation epoch 0: 100%|██████████| 33/33 [00:19<00:00,  1.68it/s]


SUMMARY OF EPOCH 0
├── Training
│   ├── Ppyoloeloss/loss = 2.0001
│   ├── Ppyoloeloss/loss_cls = 1.2117
│   ├── Ppyoloeloss/loss_dfl = 0.8801
│   └── Ppyoloeloss/loss_iou = 0.1393
└── Validation
    ├── F1@0.50 = 0.1523
    ├── F1@0.50:0.95 = 0.1188
    ├── Map@0.50 = 0.5462
    ├── Map@0.50:0.95 = 0.4075
    ├── Ppyoloeloss/loss = 1.6469
    ├── Ppyoloeloss/loss_cls = 0.887
    ├── Ppyoloeloss/loss_dfl = 0.8774
    ├── Ppyoloeloss/loss_iou = 0.1285
    ├── Precision@0.50 = 0.09
    ├── Precision@0.50:0.95 = 0.0709
    ├── Recall@0.50 = 0.8095
    └── Recall@0.50:0.95 = 0.6065



[2023-06-28 18:14:41] INFO - base_sg_logger.py - Checkpoint saved in notebook_ckpts/YOLONAS_6/ckpt_best.pth
[2023-06-28 18:14:41] INFO - sg_trainer.py - Best checkpoint overriden: validation mAP@0.50: 0.5462343692779541
Validation epoch 1: 100%|██████████| 33/33 [00:20<00:00,  1.59it/s]


...

Validation epoch 149: 100%|██████████| 33/33 [00:06<00:00,  5.03it/s]


SUMMARY OF EPOCH 149
├── Training
│   ├── Ppyoloeloss/loss = 1.0581
│   │   ├── Best until now = 1.0494 (↗ 0.0087)
│   │   └── Epoch N-1      = 1.0515 (↗ 0.0066)
│   ├── Ppyoloeloss/loss_cls = 0.5201
│   │   ├── Best until now = 0.5143 (↗ 0.0059)
│   │   └── Epoch N-1      = 0.5155 (↗ 0.0047)
│   ├── Ppyoloeloss/loss_dfl = 0.6701
│   │   ├── Best until now = 0.6664 (↗ 0.0037)
│   │   └── Epoch N-1      = 0.6668 (↗ 0.0033)
│   └── Ppyoloeloss/loss_iou = 0.0812
│       ├── Best until now = 0.0803 (↗ 0.0009)
│       └── Epoch N-1      = 0.0811 (↗ 1e-04)
└── Validation
    ├── F1@0.50 = 0.5373
    │   ├── Best until now = 0.5366 (↗ 0.0007)
    │   └── Epoch N-1      = 0.5366 (↗ 0.0007)
    ├── F1@0.50:0.95 = 0.4552
    │   ├── Best until now = 0.4543 (↗ 0.0009)
    │   └── Epoch N-1      = 0.4543 (↗ 0.0009)
    ├── Map@0.50 = 0.881
    │   ├── Best until now = 0.8858 (↘ -0.0048)
    │   └── Epoch N-1      = 0.8811 (↘ -0.0)
    ├── Map@0.50:0.95 = 0.7013
    │   ├── Best until now = 0.7026 

[2023-06-28 22:09:45] INFO - sg_trainer.py - RUNNING ADDITIONAL TEST ON THE AVERAGED MODEL...
Validation epoch 150: 100%|██████████| 33/33 [00:06<00:00,  4.94it/s]


SUMMARY OF EPOCH 150
├── Training
│   ├── Ppyoloeloss/loss = 1.0581
│   │   ├── Best until now = 1.0494 (↗ 0.0087)
│   │   └── Epoch N-1      = 1.0515 (↗ 0.0066)
│   ├── Ppyoloeloss/loss_cls = 0.5201
│   │   ├── Best until now = 0.5143 (↗ 0.0059)
│   │   └── Epoch N-1      = 0.5155 (↗ 0.0047)
│   ├── Ppyoloeloss/loss_dfl = 0.6701
│   │   ├── Best until now = 0.6664 (↗ 0.0037)
│   │   └── Epoch N-1      = 0.6668 (↗ 0.0033)
│   └── Ppyoloeloss/loss_iou = 0.0812
│       ├── Best until now = 0.0803 (↗ 0.0009)
│       └── Epoch N-1      = 0.0811 (↗ 1e-04)
└── Validation
    ├── F1@0.50 = 0.4981
    │   ├── Best until now = 0.5373 (↘ -0.0392)
    │   └── Epoch N-1      = 0.5373 (↘ -0.0392)
    ├── F1@0.50:0.95 = 0.4207
    │   ├── Best until now = 0.4552 (↘ -0.0346)
    │   └── Epoch N-1      = 0.4552 (↘ -0.0346)
    ├── Map@0.50 = 0.8839
    │   ├── Best until now = 0.8858 (↘ -0.0019)
    │   └── Epoch N-1      = 0.881  (↗ 0.0029)
    ├── Map@0.50:0.95 = 0.6995
    │   ├── Best until now = 

[2023-06-28 22:09:52] INFO - base_sg_logger.py - [CLEANUP] - Successfully stopped system monitoring process


In [10]:
# Experiment 7    {'batch': 16, 'lr': 0.01, 'optimizer': 'Adam'}
model = models.get("yolo_nas_m", pretrained_weights="coco", num_classes=13)

CHECKPOINT_DIR = 'notebook_ckpts/'
trainer = Trainer(experiment_name=f'YOLONAS_7', ckpt_root_dir=CHECKPOINT_DIR)

trainer.train(
    model=model, 
    training_params=train_params_adam_001, 
    train_loader=train_loader_16, 
    valid_loader=valid_loader_16
    )

del trainer
sleep(5)

[2023-06-28 22:09:58] INFO - checkpoint_utils.py - License Notification: YOLO-NAS pre-trained weights are subjected to the specific license terms and conditions detailed in 
https://github.com/Deci-AI/super-gradients/blob/master/LICENSE.YOLONAS.md
By downloading the pre-trained weight files you agree to comply with these terms.
[2023-06-28 22:09:58] WARNING - sg_trainer.py - Train dataset size % batch_size != 0 and drop_last=False, this might result in smaller last batch.


The console stream is now moved to notebook_ckpts/YOLONAS_7/console_Jun28_22_09_58.txt


[2023-06-28 22:09:58] INFO - sg_trainer.py - Using EMA with params {'decay': 0.9997, 'decay_type': 'threshold', 'beta': 15}
[2023-06-28 22:10:01] INFO - sg_trainer_utils.py - TRAINING PARAMETERS:
    - Mode:                         Single GPU
    - Number of GPUs:               1          (1 available on the machine)
    - Dataset size:                 4097       (len(train_set))
    - Batch size per GPU:           16         (batch_size)
    - Batch Accumulate:             1          (batch_accumulate)
    - Total batch size:             16         (num_gpus * batch_size)
    - Effective Batch size:         16         (num_gpus * batch_size * batch_accumulate)
    - Iterations per epoch:         257        (len(train_loader))
    - Gradient updates per epoch:   257        (len(train_loader) / batch_accumulate)

[2023-06-28 22:10:01] INFO - sg_trainer.py - Started training for 150 epochs (0/149)

Validation epoch 0: 100%|██████████| 33/33 [00:06<00:00,  5.00it/s]


SUMMARY OF EPOCH 0
├── Training
│   ├── Ppyoloeloss/loss = 3.8853
│   ├── Ppyoloeloss/loss_cls = 1.6787
│   ├── Ppyoloeloss/loss_dfl = 2.1348
│   └── Ppyoloeloss/loss_iou = 0.4557
└── Validation
    ├── F1@0.50 = 0.0019
    ├── F1@0.50:0.95 = 0.0011
    ├── Map@0.50 = 0.0082
    ├── Map@0.50:0.95 = 0.0026
    ├── Ppyoloeloss/loss = 3.8358
    ├── Ppyoloeloss/loss_cls = 1.7535
    ├── Ppyoloeloss/loss_dfl = 1.9687
    ├── Ppyoloeloss/loss_iou = 0.4392
    ├── Precision@0.50 = 0.001
    ├── Precision@0.50:0.95 = 0.0005
    ├── Recall@0.50 = 0.0584
    └── Recall@0.50:0.95 = 0.0324



[2023-06-28 22:11:27] INFO - base_sg_logger.py - Checkpoint saved in notebook_ckpts/YOLONAS_7/ckpt_best.pth
[2023-06-28 22:11:27] INFO - sg_trainer.py - Best checkpoint overriden: validation mAP@0.50: 0.008248887024819851
Validation epoch 1: 100%|██████████| 33/33 [00:06<00:00,  4.86it/s]


...

[2023-06-29 01:55:10] INFO - base_sg_logger.py - Checkpoint saved in notebook_ckpts/YOLONAS_7/ckpt_best.pth
[2023-06-29 01:55:10] INFO - sg_trainer.py - Best checkpoint overriden: validation mAP@0.50: 0.38869091868400574
Validation epoch 149: 100%|██████████| 33/33 [00:07<00:00,  4.46it/s]


SUMMARY OF EPOCH 149
├── Training
│   ├── Ppyoloeloss/loss = 1.9448
│   │   ├── Best until now = 1.9145 (↗ 0.0303)
│   │   └── Epoch N-1      = 1.9145 (↗ 0.0303)
│   ├── Ppyoloeloss/loss_cls = 0.9995
│   │   ├── Best until now = 0.9829 (↗ 0.0166)
│   │   └── Epoch N-1      = 0.9829 (↗ 0.0166)
│   ├── Ppyoloeloss/loss_dfl = 1.0203
│   │   ├── Best until now = 1.0074 (↗ 0.0129)
│   │   └── Epoch N-1      = 1.0074 (↗ 0.0129)
│   └── Ppyoloeloss/loss_iou = 0.174
│       ├── Best until now = 0.1711 (↗ 0.0029)
│       └── Epoch N-1      = 0.1711 (↗ 0.0029)
└── Validation
    ├── F1@0.50 = 0.0896
    │   ├── Best until now = 0.0905 (↘ -0.0009)
    │   └── Epoch N-1      = 0.0896 (↗ 0.0)
    ├── F1@0.50:0.95 = 0.0651
    │   ├── Best until now = 0.0656 (↘ -0.0005)
    │   └── Epoch N-1      = 0.0651 (↘ -0.0)
    ├── Map@0.50 = 0.3892
    │   ├── Best until now = 0.3887 (↗ 0.0005)
    │   └── Epoch N-1      = 0.3887 (↗ 0.0005)
    ├── Map@0.50:0.95 = 0.2424
    │   ├── Best until now = 0.2422 (

[2023-06-29 01:56:41] INFO - base_sg_logger.py - Checkpoint saved in notebook_ckpts/YOLONAS_7/ckpt_best.pth
[2023-06-29 01:56:41] INFO - sg_trainer.py - Best checkpoint overriden: validation mAP@0.50: 0.38920876383781433
[2023-06-29 01:56:46] INFO - sg_trainer.py - RUNNING ADDITIONAL TEST ON THE AVERAGED MODEL...
Validation epoch 150: 100%|██████████| 33/33 [00:07<00:00,  4.60it/s]


SUMMARY OF EPOCH 150
├── Training
│   ├── Ppyoloeloss/loss = 1.9448
│   │   ├── Best until now = 1.9145 (↗ 0.0303)
│   │   └── Epoch N-1      = 1.9145 (↗ 0.0303)
│   ├── Ppyoloeloss/loss_cls = 0.9995
│   │   ├── Best until now = 0.9829 (↗ 0.0166)
│   │   └── Epoch N-1      = 0.9829 (↗ 0.0166)
│   ├── Ppyoloeloss/loss_dfl = 1.0203
│   │   ├── Best until now = 1.0074 (↗ 0.0129)
│   │   └── Epoch N-1      = 1.0074 (↗ 0.0129)
│   └── Ppyoloeloss/loss_iou = 0.174
│       ├── Best until now = 0.1711 (↗ 0.0029)
│       └── Epoch N-1      = 0.1711 (↗ 0.0029)
└── Validation
    ├── F1@0.50 = 0.0902
    │   ├── Best until now = 0.0905 (↘ -0.0003)
    │   └── Epoch N-1      = 0.0896 (↗ 0.0006)
    ├── F1@0.50:0.95 = 0.0655
    │   ├── Best until now = 0.0656 (↘ -0.0001)
    │   └── Epoch N-1      = 0.0651 (↗ 0.0004)
    ├── Map@0.50 = 0.3831
    │   ├── Best until now = 0.3892 (↘ -0.0061)
    │   └── Epoch N-1      = 0.3892 (↘ -0.0061)
    ├── Map@0.50:0.95 = 0.2388
    │   ├── Best until now = 0

[2023-06-29 01:56:54] INFO - base_sg_logger.py - [CLEANUP] - Successfully stopped system monitoring process


In [11]:
# Experiment 8    {'batch': 16, 'lr': 0.01, 'optimizer': 'SGD'}
model = models.get("yolo_nas_m", pretrained_weights="coco", num_classes=13)

CHECKPOINT_DIR = 'notebook_ckpts/'
trainer = Trainer(experiment_name=f'YOLONAS_8', ckpt_root_dir=CHECKPOINT_DIR)

trainer.train(
    model=model, 
    training_params=train_params_sgd_001, 
    train_loader=train_loader_16, 
    valid_loader=valid_loader_16
    )

del trainer
sleep(5)

[2023-06-29 01:56:59] INFO - checkpoint_utils.py - License Notification: YOLO-NAS pre-trained weights are subjected to the specific license terms and conditions detailed in 
https://github.com/Deci-AI/super-gradients/blob/master/LICENSE.YOLONAS.md
By downloading the pre-trained weight files you agree to comply with these terms.
[2023-06-29 01:56:59] WARNING - sg_trainer.py - Train dataset size % batch_size != 0 and drop_last=False, this might result in smaller last batch.


The console stream is now moved to notebook_ckpts/YOLONAS_8/console_Jun29_01_56_59.txt


[2023-06-29 01:57:00] INFO - sg_trainer.py - Using EMA with params {'decay': 0.9997, 'decay_type': 'threshold', 'beta': 15}
[2023-06-29 01:57:02] INFO - sg_trainer_utils.py - TRAINING PARAMETERS:
    - Mode:                         Single GPU
    - Number of GPUs:               1          (1 available on the machine)
    - Dataset size:                 4097       (len(train_set))
    - Batch size per GPU:           16         (batch_size)
    - Batch Accumulate:             1          (batch_accumulate)
    - Total batch size:             16         (num_gpus * batch_size)
    - Effective Batch size:         16         (num_gpus * batch_size * batch_accumulate)
    - Iterations per epoch:         257        (len(train_loader))
    - Gradient updates per epoch:   257        (len(train_loader) / batch_accumulate)

[2023-06-29 01:57:02] INFO - sg_trainer.py - Started training for 150 epochs (0/149)

Validation epoch 0: 100%|██████████| 33/33 [00:06<00:00,  4.75it/s]


SUMMARY OF EPOCH 0
├── Training
│   ├── Ppyoloeloss/loss = 2.3337
│   ├── Ppyoloeloss/loss_cls = 1.2877
│   ├── Ppyoloeloss/loss_dfl = 1.0935
│   └── Ppyoloeloss/loss_iou = 0.1997
└── Validation
    ├── F1@0.50 = 0.0581
    ├── F1@0.50:0.95 = 0.041
    ├── Map@0.50 = 0.2624
    ├── Map@0.50:0.95 = 0.1858
    ├── Ppyoloeloss/loss = 2.0172
    ├── Ppyoloeloss/loss_cls = 1.0386
    ├── Ppyoloeloss/loss_dfl = 1.0884
    ├── Ppyoloeloss/loss_iou = 0.1737
    ├── Precision@0.50 = 0.0314
    ├── Precision@0.50:0.95 = 0.0222
    ├── Recall@0.50 = 0.6022
    └── Recall@0.50:0.95 = 0.4051



[2023-06-29 01:58:22] INFO - base_sg_logger.py - Checkpoint saved in notebook_ckpts/YOLONAS_8/ckpt_best.pth
[2023-06-29 01:58:22] INFO - sg_trainer.py - Best checkpoint overriden: validation mAP@0.50: 0.26244762539863586
Validation epoch 1: 100%|██████████| 33/33 [00:06<00:00,  4.81it/s]


...

[2023-06-29 05:25:27] INFO - base_sg_logger.py - Checkpoint saved in notebook_ckpts/YOLONAS_8/ckpt_best.pth
[2023-06-29 05:25:27] INFO - sg_trainer.py - Best checkpoint overriden: validation mAP@0.50: 0.8670172095298767
Validation epoch 149: 100%|██████████| 33/33 [00:06<00:00,  5.01it/s]


SUMMARY OF EPOCH 149
├── Training
│   ├── Ppyoloeloss/loss = 1.1742
│   │   ├── Best until now = 1.1719 (↗ 0.0022)
│   │   └── Epoch N-1      = 1.1795 (↘ -0.0054)
│   ├── Ppyoloeloss/loss_cls = 0.584
│   │   ├── Best until now = 0.5819 (↗ 0.0021)
│   │   └── Epoch N-1      = 0.5842 (↘ -0.0002)
│   ├── Ppyoloeloss/loss_dfl = 0.7124
│   │   ├── Best until now = 0.7091 (↗ 0.0034)
│   │   └── Epoch N-1      = 0.7148 (↘ -0.0024)
│   └── Ppyoloeloss/loss_iou = 0.0936
│       ├── Best until now = 0.094  (↘ -0.0005)
│       └── Epoch N-1      = 0.0952 (↘ -0.0016)
└── Validation
    ├── F1@0.50 = 0.4142
    │   ├── Best until now = 0.4158 (↘ -0.0017)
    │   └── Epoch N-1      = 0.4158 (↘ -0.0017)
    ├── F1@0.50:0.95 = 0.3474
    │   ├── Best until now = 0.3489 (↘ -0.0015)
    │   └── Epoch N-1      = 0.3489 (↘ -0.0015)
    ├── Map@0.50 = 0.8656
    │   ├── Best until now = 0.867  (↘ -0.0014)
    │   └── Epoch N-1      = 0.867  (↘ -0.0014)
    ├── Map@0.50:0.95 = 0.6717
    │   ├── Best until 

[2023-06-29 05:26:56] INFO - sg_trainer.py - RUNNING ADDITIONAL TEST ON THE AVERAGED MODEL...
Validation epoch 150: 100%|██████████| 33/33 [00:06<00:00,  5.01it/s]


SUMMARY OF EPOCH 150
├── Training
│   ├── Ppyoloeloss/loss = 1.1742
│   │   ├── Best until now = 1.1719 (↗ 0.0022)
│   │   └── Epoch N-1      = 1.1795 (↘ -0.0054)
│   ├── Ppyoloeloss/loss_cls = 0.584
│   │   ├── Best until now = 0.5819 (↗ 0.0021)
│   │   └── Epoch N-1      = 0.5842 (↘ -0.0002)
│   ├── Ppyoloeloss/loss_dfl = 0.7124
│   │   ├── Best until now = 0.7091 (↗ 0.0034)
│   │   └── Epoch N-1      = 0.7148 (↘ -0.0024)
│   └── Ppyoloeloss/loss_iou = 0.0936
│       ├── Best until now = 0.094  (↘ -0.0005)
│       └── Epoch N-1      = 0.0952 (↘ -0.0016)
└── Validation
    ├── F1@0.50 = 0.4102
    │   ├── Best until now = 0.4158 (↘ -0.0056)
    │   └── Epoch N-1      = 0.4142 (↘ -0.0039)
    ├── F1@0.50:0.95 = 0.3449
    │   ├── Best until now = 0.3489 (↘ -0.0039)
    │   └── Epoch N-1      = 0.3474 (↘ -0.0024)
    ├── Map@0.50 = 0.8636
    │   ├── Best until now = 0.867  (↘ -0.0034)
    │   └── Epoch N-1      = 0.8656 (↘ -0.002)
    ├── Map@0.50:0.95 = 0.6715
    │   ├── Best until n

[2023-06-29 05:27:03] INFO - base_sg_logger.py - [CLEANUP] - Successfully stopped system monitoring process
